# ナップサック問題

## 概要

ここに$N$個のものがあります。$i$番目のものの重さと価値をそれぞれ$w_i, v_i$とします。これらをナップサックに入れることを考えているのですが、ナップサックには$W$までしか入れることができません。このときナップサックに入れたものの価値の合計を最大にしつつ、入れたものの重さの合計を$W$以下にするような組み合わせはどのようなものでしょうか、という組合せ最適化問題です。  
この問題はNP困難な問題であることが知られています。

## 応用例: 航空機に積載する荷物の最適化

航空機に荷物のコンテナを詰め込む際に、どのような組み合わせをすれば荷重制限を満たしつつ、1回で運ぶ積載重量を最大にできかを考える問題です。ここでいう荷重制限とは、最大積載重量以下でなければならないという制約のほかに、コンテナの大きさや置ける位置に対するものも含まれます。  
さらにはコンテナの配置によっては航空機全体の重心が変化し、飛行中の姿勢制御に追加の燃料が必要となってしまいます。このため、重心に関する制約や飛行機全体の歪みも抑える制約なども考慮する必要があります。

![重心位置と歪みに対する制約](./images/knapsack_01.png)

## 応用例: ポートフォリオ最適化

リスクを最小にしつつ予想収益を最大にする資産投資を考えるのが、ポートフォリオ最適化問題です。例えば株の運用を考えましょう。購入できる株式数には制限があるのでこれを守りつつ利益を最大化する問題は、ナップサック問題と同じ文脈で考えることが可能です。  
今回はこのナップサック問題を解くために、JijModelingとJijZeptを用いてみましょう。

# 数理モデル立案

以下ではナップサックに入れることができる最大重量$W$、$i$番目のものの重さと価値$w_i, v_i$などは全て整数とします。

## バイナリ変数

$i$番目のものをナップサックに入れるとき$x_i = 1$、そうでないとき$x_i=0$となるようなバイナリ変数$x_i$を用いて定式化を行いましょう。

## 制約: ナップサックの重量制限

ナップサックに入れることができる総重量を$W$とすると、これは数式で

$$\sum_{i=1}^{N} w_i x_i \leq W \tag{1}$$

のようになります。$x_i$は0か1の変数であるため、ナップサックに入れる($x_i=1$)ものの重さ$w_i$のみが加算されます。

## 目的関数

問題から、最大にしたいのはナップサックに入れたものの価値の合計です。よって

$$\mathrm{obj} = - \sum_{i=1}^{N} v_i x_i \tag{2} $$

# 実装しましょう

それでは実際にJijのプロダクトを用いて、この問題を解くためのPythonスクリプトを作成しましょう。

## JijModelingで問題作成

### 問題の作成と初期化

In [1]:
import jijmodeling as jm

# set problem
problem = jm.Problem('knapsack')

### 変数の定義

以下のようにして、種々の変数を定義します。

In [2]:
# define variables
values = jm.Placeholder('values', dim=1)
N = values.shape[0]
weights = jm.Placeholder('weights', shape=(N))
W = jm.Placeholder('W')
x = jm.Binary('x', shape=(N))
i = jm.Element('i', (0, N))

`values`はナップサックに入れる予定のものの価値が格納された1次元リスト、`weights`はもの重さが格納された1次元リストです。また`W`はナップサックに入れることができる最大総重量を表します。`N`はナップサックに入れようとしているものの総数ですが、ここでは`values`の長さからこれを判断しています。さらにこの`N`を用いて`weights`の長さ(shape)を指定することで、`values`と`weights`の長さが一致するようにしています。

### 制約の実装

(1)式を実装していきましょう。

In [3]:
# set total weight constraint
const = jm.Sum(i, weights[i]*x[i])
problem += jm.Constraint('h1', const<=W)

### 目的関数の実装

続いて(2)式の実装です。

In [4]:
# set objective function
obj = - jm.Sum(i, values[i]*x[i])
problem += obj

ここで作成した問題を表示してみましょう。

In [5]:
problem

### インスタンスの作成

実際に解きたい問題の数値を与えることで、実際にナップサックにものを入れる問題を解いていきましょう。

In [6]:
# set a list of values & weights 
inst_values = [1, 2, 3, 4, 5, 6, 7, 8, 9, 10]
inst_weights = [4, 9, 2, 5, 10, 7, 6, 8, 10, 9]
# set maximum weight
inst_W = 30
instance_data = {'values': inst_values, 'weights': inst_weights, 'W': inst_W}

先ほど定義した`values`, `weights`, `W`の具体的な値を決定します。これを後ほど`JijZept`を用いて計算するために、辞書に格納します。

### 未定乗数の決定

`h1`という制約を設定したため、それに対応する未定乗数を$\lambda_1$を設定しましょう。ここでは適当に11.0としています。

In [7]:
# set multipliers
lam1 = 11.0
multipliers = {'h1': lam1}

### JijZeptで問題を解く

それでは`JijZept`のSAを用いて、この問題の最適解を求めます。

In [8]:
import jijzept as jz

# set sampler
sampler = jz.JijSASampler(config='./config.toml')
# solve problem
response = sampler.sample_model(problem, instance_data, multipliers, 
                                num_reads=200, num_sweeps=100)

uploading instance ...
submitting query ...
submitted to the queue.
Your solution_id is ca50dbb86edf4ea4ad9381be6ed8ba1e.


### 解析しやすくする

出てきた結果を解析しやすくするために、decodeを行いましょう。

In [9]:
# decode solution
decoded = problem.decode(response, instance_data, {})

### 結果の可視化

エネルギーが一番低い解だけを取り出し、その解がどのようなものかを見てみましょう。

In [10]:
def visualize_solution(decoded):
    x = decoded.solutions[0]['x']
    print(decoded.constraint_violations[0])
    in_knapsack = []
    total_weight = 0
    total_value = 0
    for i, j in enumerate(x):
        if j == 1:
            in_knapsack.append(i)
            total_value += inst_values[i]
            total_weight += inst_weights[i]
    print(in_knapsack)
    print('Total value : ', total_value)
    print('Total weight : ', total_weight)

visualize_solution(decoded)

{'h1': 1.0}
[1, 3, 7, 9]
Total value :  24
Total weight :  31


## パラメータサーチ機能をONにする

### パラメータサーチ機能とは?

先ほどは$\lambda_1 = 11.0$としていましたが、この定数を適当な値(例えば$\lambda_1 = 10000000$)に変更して解いてみましょう

In [11]:
# set multipliers
lam1 = 10000000
multipliers = {'h1': lam1}
# set sampler
sampler = jz.JijSASampler(config='./config.toml')
# solve problem
response = sampler.sample_model(problem, instance_data, multipliers, 
                                num_reads=200, num_sweeps=100)
# decode solution
decoded = problem.decode(response, instance_data, {})
visualize_solution(decoded)

uploading instance ...
submitting query ...
submitted to the queue.
Your solution_id is 51cdfa7a09db44028717674f09a81b9b.
{'h1': 1.0}
[0, 2, 4, 5, 7]
Total value :  23
Total weight :  31


$\lambda_1$は制約`h1`の重みを表す定数です。今の場合、先ほどよりもこの重みを大きくしたため、`h1`が満たされやすい状況が作られています。しかし、$\lambda_1 h_1 \gg |\mathrm{obj}|$から、$\mathrm{obj}$を最小化する目的が蔑ろにされてしまい、ナップサックにいれるものの価値の合計が先ほどより小さくなっています。  
次は$\lambda_1=0.001$のように極端に小さくしてみましょう。

In [12]:
# set multipliers
lam1 = 0.001
multipliers = {'h1': lam1}
# set sampler
sampler = jz.JijSASampler(config='./config.toml')
# solve problem
response = sampler.sample_model(problem, instance_data, multipliers, 
                                num_reads=200, num_sweeps=100)
# decode solution
decoded = problem.decode(response, instance_data, {})
# visualize soluiton
visualize_solution(decoded)

uploading instance ...
submitting query ...
submitted to the queue.
Your solution_id is 2ce10727f91e431690b08103833546fb.
{'h1': 40.0}
[0, 1, 2, 3, 4, 5, 6, 7, 8, 9]
Total value :  55
Total weight :  70


今度は制約`h1`が満たされていない解が発見されました。これは$\lambda_1$を極端に小さくしたために、$h_1=0$よりも$\mathrm{obj}$を最小化することが優先されたためです。  
これらの数値実験結果から、「制約を満たしつつ目的関数を最小にする」ような丁度良い未定乗数$\lambda_1$を選ぶ必要があることがわかります。では$\lambda_1$はどのように推定すれば良いのでしょうか。実は`JijZept`にはその推定を行い、ほどよい未定乗数を探索するパラメータサーチ機能が備わっています。

### パラメータサーチ機能を用いたスクリプト

それには以下のようにスクリプトを変更します。

In [13]:
lam1 = 1.0
multipliers = {'h1': lam1}
response = sampler.sample_model(problem, instance_data, multipliers, 
                                num_reads=200, num_sweeps=100, search=True)

uploading instance ...
submitting query ...
submitted to the queue.
Your solution_id is 950d2a340bc94448a47efc47aa760a3a.


ここではパラメータサーチを始める初期の$\lambda_1$を1.0としています。  
`sampler.sample_model`の`search`引数に`True`を入力することで、パラメータサーチ機能を用いることができます。`JijZept`のパラメータサーチ機能によって、$\lambda_1$がどのような値に収束したのかを見てみましょう。

In [14]:
response.info

{'sampling_time': 107383.04816186428}

こうして出力された`response`をdecodeしたものを表示してみましょう。

In [15]:
decoded = problem.decode(response, instance_data, {})
print('length: {}'.format(len(decoded)))
decoded[:3]

print(decoded.solutions)
print(decoded.objectives)
print(decoded.constraint_expr_value)
print(decoded.constraint_violations)

length: 2000
[{'x': array([0., 0., 0., 1., 0., 1., 0., 0., 1., 1.])}
 {'x': array([0., 0., 0., 0., 1., 1., 1., 1., 0., 0.])}
 {'x': array([0., 1., 1., 1., 0., 1., 1., 0., 0., 0.])} ...
 {'x': array([1., 1., 1., 1., 1., 1., 1., 1., 1., 1.])}
 {'x': array([1., 1., 1., 1., 1., 1., 1., 1., 1., 1.])}
 {'x': array([1., 1., 1., 1., 1., 1., 1., 1., 1., 1.])}]
[-29. -26. -22. ... -55. -55. -55.]
[{'h1': {(): 1.0}} {'h1': {(): 1.0}} {'h1': {(): -1.0}} ...
 {'h1': {(): 40.0}} {'h1': {(): 40.0}} {'h1': {(): 40.0}}]
[{'h1': 1.0} {'h1': 1.0} {'h1': 0.0} ... {'h1': 40.0} {'h1': 40.0}
 {'h1': 40.0}]


この`decoded`には制約を満たしていないものも含まれるため、最小エネルギーのものを抽出しようにも制約が満たされていない可能性があります。よって以下のようにして制約が満たされた解(実行可能解)を抽出しましょう。

In [16]:
import numpy as np

feasibles = decoded.feasibles()
print(feasibles)

[({'x': array([0., 1., 1., 1., 0., 1., 1., 0., 0., 0.])}, -471.5, 1, -22., {'h1': 0.0}, {'h1': {(): -1.0}}, {})
 ({'x': array([1., 0., 1., 1., 0., 0., 0., 1., 1., 0.])}, -474.5, 1, -25., {'h1': 0.0}, {'h1': {(): -1.0}}, {})
 ({'x': array([1., 1., 0., 0., 0., 0., 0., 1., 0., 1.])}, -471. , 1, -21., {'h1': 0.0}, {'h1': {(): 0.0}}, {})
 ({'x': array([0., 0., 1., 1., 1., 1., 1., 0., 0., 0.])}, -475. , 1, -25., {'h1': 0.0}, {'h1': {(): 0.0}}, {})
 ({'x': array([0., 0., 1., 1., 0., 0., 1., 1., 0., 1.])}, -482. , 1, -32., {'h1': 0.0}, {'h1': {(): 0.0}}, {})
 ({'x': array([1., 0., 0., 1., 0., 1., 1., 1., 0., 0.])}, -476. , 1, -26., {'h1': 0.0}, {'h1': {(): 0.0}}, {})
 ({'x': array([0., 0., 1., 0., 0., 0., 0., 1., 1., 1.])}, -479.5, 1, -30., {'h1': 0.0}, {'h1': {(): -1.0}}, {})
 ({'x': array([0., 0., 1., 0., 0., 0., 0., 1., 1., 1.])}, -479.5, 1, -30., {'h1': 0.0}, {'h1': {(): -1.0}}, {})
 ({'x': array([1., 0., 1., 0., 0., 0., 1., 1., 1., 0.])}, -478. , 1, -28., {'h1': 0.0}, {'h1': {(): 0.0}}, {

すると先ほどとは違い、制約条件が全て満たされたもののみ表示されます。このようにして抽出された実行可能解の中から最小エネルギーのものを用いることで、最適解の状態を確認することができます。

# 結言

今回はナップサック問題から、JijModelingとJijZeptの使い方をご紹介しました。以下に要点をまとめます。

- JijModelingは不等式制約も簡単に表現することができる。
- JijZeptではJijSASampler(...).sample_model(search=True)とすることで、制約の係数である未定乗数の程よい値の大きさを自動探索する機能を使うことができる。
- パラメータサーチ機能を用いた場合、`response.info['para_search']['search_history']`から未定乗数の探索推移を確認することができる。
- decodeされた結果から、制約が全て満たされた実行可能解(feasible solution)のみを`decoded.feasibles()`により抽出することができる。

JijModelingとJijZeptの便利機能を駆使して、最適解を発見するのが困難な問題にも挑戦していきましょう。

# 参考文献

[1] [Lucas, 2013, "Ising formulations of many NP problems"](https://www.frontiersin.org/articles/10.3389/fphy.2014.00005/full)  
[2] [OpenJij チュートリアル, 8-Solving Knapsack Problem with PyQUBO](https://openjij.github.io/OpenJijTutorial/build/html/ja/008-KnapsackPyqubo.html)  
[3] [Jij Tech Blog, 「ナップサック問題が量子アニーリング(QA)で解けない」は本当か？](https://jijtech.hatenablog.com/entry/2020/11/06/004203)  
[4] [Jij Tech Blog, 「航空機荷物搭載最適化問題」](https://jijtech.hatenablog.com/entry/2021/02/26/083843)  
[5] [Pilon et al., 2021, "Aircraft Loading Optimization -- QUBO models under multiple constraints"](https://arxiv.org/abs/2102.09621)  
[6] [Airbus Quantum Computing Challenge, Problem Statement 5, Aircraft Loading Optimisation](https://www.airbus.com/innovation/industry-4-0/quantum-technologies/airbus-quantum-computing-challenge.html)  
[7] Kellerer et al., 2003, "Knapsack Problems"